<a href="https://colab.research.google.com/github/lindangulopez/5th_edition_examples/blob/master/FR_Copy_of_supplement_lonboard_leafmap.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

### Visualizing Large Vector Datasets with Lonboard

[Lonboard](https://github.com/developmentseed/lonboard) is a deck-gl based Python library that allows you to interactively visualize large vector datasets. You can use Lonboard in Leafmap via the [deckgl module](https://leafmap.org/deckgl/).

Lonboard uses a different terminology for different types of vector layers.

* [ScatterplotLayer](https://developmentseed.org/lonboard/latest/api/layers/scatterplot-layer/): Reders points as circles.
* [PathLayer](https://developmentseed.org/lonboard/latest/api/layers/path-layer/): Renders polylines.
* [SolidPolygonLayer](https://developmentseed.org/lonboard/latest/api/layers/solid-polygon-layer/): Renders filled and/or extruded polygons.

When visualizing vector data via lonboard, please refer to the documentation for appropriate class for the parameter values.

We will visualize and style a very large layer of rivers using Leafmap and Lonboard.

<img src='https://courses.spatialthoughts.com/images/python_dataviz/lonboard_rivers.png' width=800/>

#### Setup and Data Download

In [1]:
%%capture
if 'google.colab' in str(get_ipython()):
  !pip install leafmap lonboard palettable

In [2]:
import os
import leafmap.deckgl as leafmap
import geopandas as gpd
import pandas as pd
import requests
import palettable
import lonboard


In [3]:
data_folder = 'data'
output_folder = 'output'

if not os.path.exists(data_folder):
    os.mkdir(data_folder)
if not os.path.exists(output_folder):
    os.mkdir(output_folder)

In [4]:
def download(url):
    filename = os.path.join(data_folder, os.path.basename(url))
    if not os.path.exists(filename):
      with requests.get(url, stream=True, allow_redirects=True) as r:
          with open(filename, 'wb') as f:
              for chunk in r.iter_content(chunk_size=8192):
                  f.write(chunk)
      print('Downloaded', filename)

In [5]:
countries_file = 'ne_10m_admin_0_countries_ind.zip'

data_url = 'https://github.com/spatialthoughts/python-dataviz-web/releases/download/'

# This is a subset of the main HydroRivers dataset of all
# rivers having `UPLAND_SKM` value  greater than 100 sq. km.
hydrorivers_file = 'hydrorivers_100.gpkg'
hydrorivers_url = data_url + 'hydrosheds/'

countries_file = 'ne_10m_admin_0_countries_ind.zip'
countries_url = data_url + 'naturalearth/'


download(hydrorivers_url + hydrorivers_file)
download(countries_url + countries_file)

Downloaded data/hydrorivers_100.gpkg
Downloaded data/ne_10m_admin_0_countries_ind.zip


#### Data Pre-Processing

Read the countries shapefile.

In [6]:
countries_filepath = os.path.join(data_folder, countries_file)

For the assignment, you need to pick the country for which you want to create the map. We can print a list of values from the `SOVEREIGNT` column of `country_gdf` GeoDataFrame using `country_gdf.SOVEREIGNT.values` to know the names of all countries.

In [7]:
country_gdf = gpd.read_file(countries_filepath)
print(sorted(country_gdf.SOVEREIGNT.unique()))

['Afghanistan', 'Albania', 'Algeria', 'Andorra', 'Angola', 'Antarctica', 'Antigua and Barbuda', 'Argentina', 'Armenia', 'Australia', 'Austria', 'Azerbaijan', 'Bahrain', 'Bangladesh', 'Barbados', 'Belarus', 'Belgium', 'Belize', 'Benin', 'Bhutan', 'Bir Tawil', 'Bolivia', 'Bosnia and Herzegovina', 'Botswana', 'Brazil', 'Brazilian Island', 'Brunei', 'Bulgaria', 'Burkina Faso', 'Burundi', 'Cabo Verde', 'Cambodia', 'Cameroon', 'Canada', 'Central African Republic', 'Chad', 'Chile', 'China', 'Colombia', 'Comoros', 'Costa Rica', 'Croatia', 'Cuba', 'Cyprus', 'Czechia', 'Democratic Republic of the Congo', 'Denmark', 'Djibouti', 'Dominica', 'Dominican Republic', 'East Timor', 'Ecuador', 'Egypt', 'El Salvador', 'Equatorial Guinea', 'Eritrea', 'Estonia', 'Ethiopia', 'Federated States of Micronesia', 'Fiji', 'Finland', 'France', 'Gabon', 'Gambia', 'Georgia', 'Germany', 'Ghana', 'Greece', 'Grenada', 'Guatemala', 'Guinea', 'Guinea-Bissau', 'Guyana', 'Haiti', 'Honduras', 'Hungary', 'Iceland', 'India', '

Select a country name. Replace the value below with your chosen country.

In [8]:
country = 'United States of America'

Apply filters to select the country feature. We use an additional filter `TYPE != 'Dependency'` to exclude overseas territories. You may have to adjust the filter to get the correct country polygon.

In [9]:
selected_country = country_gdf[
    (country_gdf['SOVEREIGNT'] == country) &
    (country_gdf['TYPE'] != 'Dependency')
]
selected_country

ADM0_A3_IN       featurecla  scalerank  LABELRANK  \
150        USA  Admin-0 country          0          2   

                   SOVEREIGNT SOV_A3  ADM0_DIF  LEVEL     TYPE TLC  ...  \
150  United States of America    US1         1      2  Country   1  ...   

    FCLASS_TR FCLASS_ID  FCLASS_PL FCLASS_GR FCLASS_IT  FCLASS_NL FCLASS_SE  \
150      None      None       None      None      None       None      None   

    FCLASS_BD  FCLASS_UA                                           geometry  
150      None       None  MULTIPOLYGON (((-122.75302 48.99251, -122.6532...  

[1 rows x 169 columns]

We read the river network data from HydroRivers. We specify the `mask` parameter which clips the layer to the country boundary while reading the data.

*This step can take a few minutes depending on the size of the country.*

In [10]:
hydrorivers_filepath = os.path.join(data_folder, hydrorivers_file)
river_gdf = gpd.read_file(hydrorivers_filepath, mask=selected_country)
river_gdf

HYRIV_ID  NEXT_DOWN  MAIN_RIV  LENGTH_KM  DIST_DN_KM  DIST_UP_KM  \
0       70591717   70587932  70598017      24.69       402.5        29.3   
1       70498826   70495296  70367865      18.82       951.8        22.2   
2       70479347   70470782  70367865      38.53       812.7        44.3   
3       70545506   70545507  70549864       1.98        42.0        78.9   
4       70545505   70545506  70549864       2.79        44.0        77.0   
...          ...        ...       ...        ...         ...         ...   
180625  80129542   80128388  80176904       7.79      1047.4        27.9   
180626  80129651   80129542  80176904       0.50      1055.2        20.1   
180627  80130164   80128388  80176904       8.51      1047.3        29.4   
180628  80130852   80130164  80176904       4.78      1055.8        20.8   
180629  80130963   80130852  80176904       1.68      1060.5        16.2   

        CATCH_SKM  UPLAND_SKM  ENDORHEIC  DIS_AV_CMS  ORD_STRA  ORD_CLAS  \
0          104.18       104.2          0       1.660         1         2   
1          113.08       113.1          0       1.564         1         2   
2          316.66       316.7          0       3.418         1         2   
3            4.71      1970.8          0      41.769         5         1   
4            6.17      1937.1          0      41.112         5         1   
...           ...         ...        ...         ...       ...       ...   
180625      17.81       178.0          0       1.700         2         5   
180626       0.09       143.8          0       1.353         2         5   
180627      29.41       229.5          0       2.363         3         4   
180628      24.73       159.2          0       1.671         3         4   
180629       6.35       125.1          0       1.315         3         4   

        ORD_FLOW   HYBAS_L12  \
0              6  7120557670   
1              6  7120472440   
2              6  7120451090   
3              5  7120519420   
4              5  7120519420   
...          ...         ...   
180625         6  8120177660   
180626         6  8120177660   
180627         6  8120177650   
180628         6  8120177650   
180629         6  8120177650   

                                                 geometry  
0       MULTILINESTRING ((-79.32083 39.10417, -79.3104...  
1       MULTILINESTRING ((-78.69167 42.575, -78.69792 ...  
2       MULTILINESTRING ((-78.99792 43.28333, -78.9979...  
3       MULTILINESTRING ((-74.24375 40.88958, -74.2395...  
4       MULTILINESTRING ((-74.26875 40.89375, -74.2645...  
...                                                   ...  
180625  MULTILINESTRING ((-155.72292 65.07292, -155.72...  
180626  MULTILINESTRING ((-155.71875 65.06875, -155.72...  
180627  MULTILINESTRING ((-155.85208 65.04792, -155.84...  
180628  MULTILINESTRING ((-155.91458 65.02292, -155.91...  
180629  MULTILINESTRING ((-155.94375 65.01875, -155.91...  

[180630 rows x 15 columns]

#### Visualize GeoDataFrame using Lonboard

Lonboard renders line layers using the [`PathLayer`](https://developmentseed.org/lonboard/latest/api/layers/path-layer/) object. We supply the lonboard parameters as keyword arguents to leafmap.

In [11]:
m = leafmap.Map(height=600)
m.add_gdf(river_gdf,
          zoom_to_layer=True,
          pickable=True,
          get_width=2,
          get_color='blue',
          width_units='pixels'
)
m

Map(custom_attribution='', layers=(PathLayer(get_color=(0, 0, 255, 255), get_width=2.0, table=arro3.core.Table…

We want to style the rivers so that the width of the line is proportional to the value in the `UPLAND_SKM` attribute. We add a new column `width` to the GeoDataFrame by scaling the input values to a range of target widths.

In [12]:
original_min = 300
original_max = 10000
target_min = 0.1
target_max = 1
scaled = (river_gdf['UPLAND_SKM'] - original_min) / (original_max - original_min)
river_gdf['width'] = scaled.clip(0, 1) * (target_max - target_min) + target_min
river_gdf_final = river_gdf.sort_values(['UPLAND_SKM', 'width'])[
    ['MAIN_RIV', 'UPLAND_SKM', 'width', 'geometry']]
river_gdf_final

MAIN_RIV  UPLAND_SKM  width  \
2999   70367865       100.1    0.1   
4677   70777275       100.1    0.1   
5507   70814357       100.1    0.1   
9658   70814357       100.1    0.1   
13035  70671630       100.1    0.1   
...         ...         ...    ...   
64547  70814357   3179206.0    1.0   
64546  70814357   3179251.0    1.0   
64201  70814357   3179311.0    1.0   
64199  70814357   3179441.0    1.0   
64203  70814357   3179496.0    1.0   

                                                geometry  
2999   MULTILINESTRING ((-83.38542 43.64375, -83.3854...  
4677   MULTILINESTRING ((-83.38125 33.15625, -83.3687...  
5507   MULTILINESTRING ((-81.40208 40.83958, -81.3979...  
9658   MULTILINESTRING ((-79.91458 41.11042, -79.9187...  
13035  MULTILINESTRING ((-79.00208 37.25625, -78.9979...  
...                                                  ...  
64547  MULTILINESTRING ((-89.80625 29.58125, -89.8020...  
64546  MULTILINESTRING ((-89.60208 29.42292, -89.6062...  
64201  MULTILINESTRING ((-89.48958 29.34792, -89.4854...  
64199  MULTILINESTRING ((-89.35625 29.28958, -89.3520...  
64203  MULTILINESTRING ((-89.31875 29.25625, -89.2979...  

[180630 rows x 4 columns]

We want to assign a color based on the `MAIN_RIV` attribute. We will split the rivers into 10 equal bins.

In [13]:
river_gdf_final['color'] = pd.qcut(
    river_gdf_final.MAIN_RIV, q=10,
    labels=False, duplicates='drop')
river_gdf_final

MAIN_RIV  UPLAND_SKM  width  \
2999   70367865       100.1    0.1   
4677   70777275       100.1    0.1   
5507   70814357       100.1    0.1   
9658   70814357       100.1    0.1   
13035  70671630       100.1    0.1   
...         ...         ...    ...   
64547  70814357   3179206.0    1.0   
64546  70814357   3179251.0    1.0   
64201  70814357   3179311.0    1.0   
64199  70814357   3179441.0    1.0   
64203  70814357   3179496.0    1.0   

                                                geometry  color  
2999   MULTILINESTRING ((-83.38542 43.64375, -83.3854...      0  
4677   MULTILINESTRING ((-83.38125 33.15625, -83.3687...      3  
5507   MULTILINESTRING ((-81.40208 40.83958, -81.3979...      4  
9658   MULTILINESTRING ((-79.91458 41.11042, -79.9187...      4  
13035  MULTILINESTRING ((-79.00208 37.25625, -78.9979...      2  
...                                                  ...    ...  
64547  MULTILINESTRING ((-89.80625 29.58125, -89.8020...      4  
64546  MULTILINESTRING ((-89.60208 29.42292, -89.6062...      4  
64201  MULTILINESTRING ((-89.48958 29.34792, -89.4854...      4  
64199  MULTILINESTRING ((-89.35625 29.28958, -89.3520...      4  
64203  MULTILINESTRING ((-89.31875 29.25625, -89.2979...      4  

[180630 rows x 5 columns]

We create a discreate colormap by assigning a color to each bin.

In [14]:
cmap = palettable.colorbrewer.diverging.Spectral_10

colormap = {}
for i, color in enumerate(cmap.colors):
    colormap[i] = color
colormap

{0: [158, 1, 66],
 1: [213, 62, 79],
 2: [244, 109, 67],
 3: [253, 174, 97],
 4: [254, 224, 139],
 5: [230, 245, 152],
 6: [171, 221, 164],
 7: [102, 194, 165],
 8: [50, 136, 189],
 9: [94, 79, 162]}

In [15]:
basemap = lonboard.basemap.CartoBasemap.DarkMatterNoLabels
cmap = palettable.colorbrewer.diverging.Spectral_10
widths = river_gdf_final['width']
colors = lonboard.colormap.apply_categorical_cmap(
    river_gdf_final['color'], colormap)

m = leafmap.Map(height=700, basemap_style=basemap)
m.add_gdf(river_gdf_final,
          zoom_to_layer=True,
          pickable=True,
          get_width=widths,
          get_color=colors,
          width_units='pixels'
)
m

Map(basemap_style=<CartoBasemap.DarkMatterNoLabels: 'https://basemaps.cartocdn.com/gl/dark-matter-nolabels-gl-…